# EIS Fire Visualizations Notebook 1.0.0
### Version: 06.10.21
EIS – Fire: Visualizations Notebooks aims to create interactive visualizations of IMERG and other raster data. These are interactive visualizations of raster data in conjunction with vector layers with added functionality including (but not limited to) time-series averages, animations.

In [1]:
from datetime import datetime
from dask.distributed import Client
import io
import numpy as np
import pandas
import os
import requests
import random
import s3fs
import warnings
import xarray as xr
import zipfile

import cartopy.crs as ccrs
import colorcet as cc
import geopandas as gpd
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
from ipyleaflet import Map, basemaps, basemap_to_tiles, DrawControl
import panel as pn
import rioxarray as rxr
from shapely.geometry import mapping

from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session, sessionmaker, declarative_base
from sqlalchemy import create_engine, MetaData, Table, inspect, and_, between, distinct
from sqlalchemy import select, func, distinct, between, and_, or_, not_, Integer

xr.set_options(display_style="html")
warnings.filterwarnings('ignore')
pn.extension()

### postgresql login credentials

In [2]:
username = 'guest'
password = 'fires'
host = 'eis-fire-db.ccgflq7ivofg.us-east-1.rds.amazonaws.com'
database = 'eisfire'
engine = 'postgresql://{}:{}@{}/{}'.format(username, password, host, database)
engine = create_engine(engine)
Base = automap_base()
Base.prepare(engine, reflect=True)
Fires = Base.classes.fires
States = Base.classes.tl_2020_us_state
Countries = Base.classes.tl_2020_us_county

### Datasets

Add, modify or remove the desired Zarr dataset file. Following the convention:
`"DATASET" : "path/to/zarr/file.zarr"`

In [3]:
raster_filepath = {
    'IMERG': "eis-dh-fire/imerg-fwi.zarr",
    'GOES FP': "eis-dh-fire/geos-fp-zarr/conus.zarr",
    'QFED': 'eis-dh-fire/qfed.zarr/',
    'GFED NRT': 'eis-dh-fire/gfed-nrt.zarr'
}

In [4]:
# TROPOMI DATA
base_path = '/home/jovyan/efs/eis-fire-tropomi'
tropomi_filepath = {
    'AEROSOL-INDEX': "tropomi_aer_ai.zarr",
    'CH4': "tropomi_ch4.zarr",
    'CO': 'tropomi_co.zarr',
    'NO2': 'tropomi_no2.zarr',
    'OZONE': 'tropomi_o3.zarr'    
}
for k, v in tropomi_filepath.items():
    tropomi_filepath[k] = os.path.join(base_path, v)

## User-defined variables

Add, modify, or remove variables below. Please follow conventions outlined in comments.

In [5]:
# ---
# Variables from raster datasets to use.
# Follow {'DATASET': ['var1', 'var2'],
#         'DATASET': ['var1', 'var2']
# ---
raster_variables = {
    'IMERG': ['IMERG.FINAL.v6_FWI'],
    'GOES FP': ['T2M', 'U2M', 'V2M'],
    'QFED': ['co.biomass'],
    'GFED NRT': ['c']
}

raster_variable_to_show = 'IMERG.FINAL.v6_FWI' #'T2M'

# If desired, slice time to date_start and date_end.
date_start = '2020-06-01'
date_end = '2020-10-01'
d_s = datetime(2020, 6, 1)
d_e = datetime(2020, 10, 1)


# See ____ for more projection options.
projection = ccrs.PlateCarree()

# Set to True if user would like to clip raster to land only.
clip_to_land = True

# If anomaly_map is True, which time step to base map off of.
# Month = 'time.month'
# Day = 'time.dayofyear'
anomaly_time_step = 'time.month'

In [6]:
tbounds = slice(date_start, date_end)
states = ["AL", "AK", "AZ", "AR", "CA", "CO", "CT", "DC", "DE", "FL", "GA", 
          "HI", "ID", "IL", "IN", "IA", "KS", "KY", "LA", "ME", "MD", 
          "MA", "MI", "MN", "MS", "MO", "MT", "NE", "NV", "NH", "NJ", 
          "NM", "NY", "NC", "ND", "OH", "OK", "OR", "PA", "RI", "SC", 
          "SD", "TN", "TX", "UT", "VT", "VA", "WA", "WV", "WI", "WY"]
markercolor_iter = ['r', 'b', 'g', 'k', 'z']
line_color_iter = ['red', 'blue', 'green', 'black', 'indianred']
daterange_iter = list(pandas.date_range(tbounds.start, tbounds.stop))
update_iter = [False, True]
cmaps  = {n: cc.palette[n] for n in ['kbc', 'fire', 'bgy', 'bgyw', 'bmy', 'gray', 'kbc']}
cmaps_str = ['kbc', 'fire', 'bgy', 'bgyw', 'bmy', 'gray']
perim_url = "https://services3.arcgis.com/T4QMspbfLg3qTGWY/arcgis/rest/services/Fire_History_Perimeters_Public/FeatureServer/0/query"
# Valid data are masks 10-15, 20-25, 30-35
goesmasks = tuple(list(range(10, 16)) + list(range(20, 26)) + list(range(30, 36)))
# Reads in a land mask to clip user-defined rasters to.
land_shp = None
if clip_to_land:
    land_shp = gpd.read_file('./shape_files/LandMask/ne_110m_land.shp')

s3 = s3fs.S3FileSystem(anon=False)
dataset_path = {}
for dataset, path in raster_filepath.items():
    print(dataset, path)
    dataset_path[dataset] = s3.get_mapper(path)

zarrDict = {}
for mission, s3_file in dataset_path.items():
    print(mission, s3_file)
    zarrDict[mission] = xr.open_zarr(s3_file, consolidated=True)

datasetSubs = {}
rasterAttrs = {}
for mission, dataset in raster_variables.items():
    for subdataset in dataset:
        if mission not in datasetSubs.keys():
            datasetSubs[mission] = {}
        rasterAttrs[subdataset] = zarrDict[mission][subdataset].attrs
        datasetSubs[mission].update({ subdataset : zarrDict[mission][subdataset]})
        
datasetSubs['GOES FP']['T2M'] = datasetSubs['GOES FP']['T2M'].resample(time='1D').mean("time").sel(time=tbounds)
datasetSubs['GOES FP']['V2M'] = datasetSubs['GOES FP']['V2M'].resample(time='1D').mean('time').sel(time=tbounds)
datasetSubs['GOES FP']['U2M'] = datasetSubs['GOES FP']['U2M'].resample(time='1D').mean('time').sel(time=tbounds)
datasetSubs['IMERG']['IMERG.FINAL.v6_FWI'] = datasetSubs['IMERG']['IMERG.FINAL.v6_FWI'].sel(time=tbounds).interp_like(datasetSubs['GOES FP']['T2M'])
datasetSubs['QFED']['co.biomass'] = datasetSubs['QFED']['co.biomass'].sel(time=tbounds).interp_like(datasetSubs['GOES FP']['T2M'])
datasetSubs['GFED NRT']['c'] = datasetSubs['GFED NRT']['c'].sel(time=tbounds).interp_like(datasetSubs['GOES FP']['T2M'])

# WS = (U2M^2 + V2M^2)^(-2)
v2m = datasetSubs['GOES FP']['V2M']
u2m = datasetSubs['GOES FP']['U2M']
datasetSubs['GOES FP']['WSA'] = (u2m**2 + v2m**2)**-2
datasetSubs['GOES FP']['WSA'] = datasetSubs['GOES FP']['WSA'].rename('WSA')

mergedDataset = None
for mission, dataDict in datasetSubs.items():
    for subd, array in dataDict.items():
        if mergedDataset is None:
            mergedDataset = array
        mergedDataset = xr.merge([mergedDataset, array])
datasetSubs = None

tropomiDict = {}
for mission, path in tropomi_filepath.items():
    print(mission, path)
    tropomiDict[mission] = xr.open_zarr(path)
tropomiVars = {}

for ds in tropomiDict.keys():
    l = list(tropomiDict[ds].variables)
    l.remove('lat')
    l.remove('lon')
    l.remove('time')
    tropomiVars[ds] = l

tropomiSubs = {}

for mission, dataset in tropomiVars.items():
    for subdataset in dataset:
        if mission not in tropomiSubs.keys():
            tropomiSubs[mission] = {}
        rasterAttrs[subdataset] = tropomiDict[mission][subdataset].attrs
        tropomiSubs[mission].update({ subdataset : tropomiDict[mission][subdataset]})

for k in tropomiSubs.keys():
    for v in tropomiSubs[k]:
        tropomiSubs[k][v] = tropomiSubs[k][v].resample(time='1D').mean('time').sel(time=tbounds)

tropoDataset = None
for mission, dataDict in tropomiSubs.items():
    for subd, array in dataDict.items():
        if tropoDataset is None:
            tropoDataset = array
        tropoDataset = xr.merge([tropoDataset, array])
tropomiSubs = None

IMERG eis-dh-fire/imerg-fwi.zarr
GOES FP eis-dh-fire/geos-fp-zarr/conus.zarr
QFED eis-dh-fire/qfed.zarr/
GFED NRT eis-dh-fire/gfed-nrt.zarr
IMERG <fsspec.mapping.FSMap object at 0x7f198267f160>
GOES FP <fsspec.mapping.FSMap object at 0x7f19822b0550>
QFED <fsspec.mapping.FSMap object at 0x7f19830c7f70>
GFED NRT <fsspec.mapping.FSMap object at 0x7f19822b05e0>
AEROSOL-INDEX /home/jovyan/efs/eis-fire-tropomi/tropomi_aer_ai.zarr
CH4 /home/jovyan/efs/eis-fire-tropomi/tropomi_ch4.zarr
CO /home/jovyan/efs/eis-fire-tropomi/tropomi_co.zarr
NO2 /home/jovyan/efs/eis-fire-tropomi/tropomi_no2.zarr
OZONE /home/jovyan/efs/eis-fire-tropomi/tropomi_o3.zarr


### Functions to query and read shape layers and data

In [7]:
def constructDataDict(mergedDataset=None, attrsDict=None):
    dataDict = dict()
    variableList = list(mergedDataset.variables)[3:] if mergedDataset else attrsDict.keys()
    varListForSum = ['c', 'co.biomass']
    for var in variableList:
        if mergedDataset:
            metadata = mergedDataset[var].attrs
        else:
            metadata = attrsDict[var]
        try:
            longName = metadata['long_name']
        except KeyError:
            longName = var
        try:
            units = metadata['units']
        except KeyError:
            units = ''
        needsCollapse = True if var in varListForSum else False
        shortName = var
        tropomiSet = True if var in list(tropoDataset.variables)[3:] else False
        dataDict[longName] = {
            'metadata': metadata,
            'units': units,
            'collapse': needsCollapse,
            'shortName': shortName,
            'tropomiSet': tropomiSet
        }
    dataDict['2-meter_wind_speed_average'] = {
        'units': 'm s-1',
        'shortName': 'WSA',
        'collapse': False,
        'tropomiSet': False
    }
    return dataDict

def getNIFCByDate(dateStart, dateEnd):
    dtStartStr = dateStart.strftime('%Y-%m-%d')
    dtEndStr = dateEnd.strftime('%Y-%m-%d')
    paramDict = {
        "where": "irwin_FireDiscoveryDateTime <= DATE '{}' AND irwin_FireOutDateTime >= DATE '{}'".format(dtStartStr, dtEndStr),
        "outFields":"*",
        "outSR":4326,
        "f":"json"
    }
    request = requests.get(url=perim_url, params=paramDict)
    data = gpd.read_file(io.BytesIO(request.content))
    return data

def get_shp_layer(engine, place):
    # INSERT CUSTOM LAYER QUERY HERE
    state_query = select(States).filter_by(stusps = place)
    # ENG INSERT CUSTOM QUERY HERE
    shpLayer = gpd.read_postgis(state_query, engine)
    shpLayer = shpLayer.rename_geometry('geometry', inplace=False)
    return shpLayer

def get_shp_data(date, engine, place='CA'):
    date_start = pandas.to_datetime(str(date))
    td = pandas.Timedelta(1, unit='D')
    date_end = (date_start+td).strftime('%Y-%m-%d')
    date_start = date_start.strftime('%Y-%m-%d')
    ### INSERT CUSTOM MARKER QUERY HERE
    fire_query = (select(Fires).
           join(States, and_(
               func.ST_CONTAINS(States.geom, Fires.geom),
               States.stusps == place,
               not_(and_(Fires.product.like("GOES-%"),
                     not_(Fires.metadata["mask"].cast(Integer()).in_((goesmasks))))),
               Fires.image_datetime > date_start, 
               Fires.image_datetime < date_end
           )).order_by(Fires.image_datetime))
    # END INSERT CUSTOM QUERY HERE
    shpData = gpd.read_postgis(fire_query, engine)
    shpData = shpData.rename_geometry('geometry', inplace=False)
    return shpData

def queryActiveFires(queryEngine, stateSelect=True, state='CA', geometryStr=None, srid='4326', dateStart='2020-06-01', dateEnd='2020-09-01', productSubStr='MOD'):
    """
    Function to query active fires given either a state to get geometry from or a shape file string.
    """
    activeFireQuery = None
    if stateSelect:
        activeFireQuery = (select(Fires.product, 
              (func.count(distinct(Fires.geom))).label("count"), 
              (func.date_trunc("day", Fires.image_datetime)).label("date")).
       group_by(Fires.product, "date").
       join(States, and_(
           func.ST_CONTAINS(States.geom, Fires.geom),
           States.stusps == state
       )).
       where(Fires.image_datetime.between(dateStart, dateEnd))
      )
    else:
        geomStr = 'SRID={};{}'.format(srid, geometryStr)
        activeFireQuery = (select(Fires.product, 
              (func.count(distinct(Fires.geom))).label("count"), 
              (func.date_trunc("day", Fires.image_datetime)).label("date")).
                           group_by(Fires.product, "date").
                           where(func.ST_CONTAINS(geomStr, Fires.geom)).
                           where(Fires.image_datetime.between(dateStart, dateEnd))
                          )
    dfFromQuery=pandas.read_sql(activeFireQuery, queryEngine)
    dfFiltered = dfFromQuery[dfFromQuery['product'].str.contains(productSubStr)]
    return dfFiltered

def clip_to_shape(raster, shape_file):
    raster.rio.set_spatial_dims(x_dim="lon", y_dim="lat", inplace=True)
    raster.rio.write_crs("epsg:4326", inplace=True)
    raster_clipped = raster.rio.clip(shape_file.geometry.apply(mapping), shape_file.crs, drop=False)
    return raster_clipped

def get_clim(data_array):
    da_min = data_array.min(dim=['lat', 'lon', 'time']).load()
    da_max = data_array.max(dim=['lat', 'lon', 'time']).load()
    return (da_min, da_max)

def get_clim_time_averaged(data_array):
    da_min = data_array.min(dim=['lat', 'lon', 'month']).load()
    da_max = data_array.max(dim=['lat', 'lon', 'month']).load()
    return (da_min, da_max)

def split_shp_data(df):
    df_mod = df[df['product'].str.contains('MOD')]
    df_goes = df[df['product'].str.contains('GOES')]
    df_v = df[df['product'].str.contains('VNP')]
    return df_goes, df_mod, df_v

def plot_points(df, fw, prj, sz, c):
    points_plt = df.hvplot.points(
        frame_width=fw,
        projection=prj,
        hover_cols=['fire_power', 'fire_confidence', 'product'],
        #marker=mk,
        size=sz,
        color=c)
    return points_plt

def plot_layer(df, fw):
    df_plt = df.hvplot(frame_width=fw, color='None')
    return df_plt

def collapseTo1D(datarray):
    dataCollapsed = datarray.sum(axis=1)
    dataCollapsed = dataCollapsed.sum(axis=1)
    return dataCollapsed

def collapseMean(datarray):
    datarray = datarray.load()
    dataCollapsed = datarray.mean(['lat'])
    dataCollapsed = dataCollapsed.mean(['lon'])
    return dataCollapsed

def getMetadata(raster):
    try:
        longname = raster.attrs['long_name']
        unit = raster.attrs['units']
    except KeyError:
        longname = raster.name
        unit = None
    return longname, unit

def timeAveragedCallBack(target, event):
    target.disabled = False if event.new == 'Time Averaged' else True

def sequentialDisable(target, event):
    target.disabled = True if event.new == 'Time Averaged' else False

### Clip raster to land mask

In [8]:
%%time
main_raster = clip_to_shape(mergedDataset[raster_variable_to_show], land_shp)
dataDict = constructDataDict(mergedDataset=None, attrsDict=rasterAttrs)

CPU times: user 91.2 ms, sys: 0 ns, total: 91.2 ms
Wall time: 90.4 ms


### Rechunk and persist data to memory

In [9]:
mergedDataset = mergedDataset.chunk({'time':-1})
tropoDataset = tropoDataset.chunk({'time':-1})

In [10]:
mergedDataset = mergedDataset.persist()

# Visualization 1 - Interactive raster plot with time series

This is a basic interactive plot. The control panel on the left give the users many options, including choosing colormaps, which state to get data from, and more.

The controls on the right allow you to zoom, move around, and save the visual. Hover over the visual to see variables.

In [11]:
timeAveragedSequentialRadioGroup = pn.widgets.RadioButtonGroup(
 name='Visualization Type', options=['Date-Time Sequential', 'Time Averaged'], value='Date-Time Sequential', button_type='success')
layersGroup = pn.widgets.CheckBoxGroup(name='Layers', options=['Active Fire Points', 'NIFC Perimeter Polygons'], value=[])
timeStepInput = pn.widgets.TextInput(name='Time Step', value='7D', disabled=True)
timeAveragedSequentialRadioGroup.link(timeStepInput, callbacks={'value': timeAveragedCallBack})
userMin = pn.widgets.IntInput(name='Min', width=60)
userMax = pn.widgets.IntInput(name='Max', width=60)
cmapSelector = pn.widgets.Select(name='Colormap Selector', value='fire', options=cmaps_str)
toggleCmapReverseV1 = pn.widgets.Toggle(name='Reverse colormap', button_type='default')
dateTimeSelector = pn.widgets.DateSlider(name='DateTime Selector', start=d_s, end=d_e, value=datetime(2020, 8, 10))
timeAveragedSequentialRadioGroup.link(dateTimeSelector, callbacks={'value': sequentialDisable})
markerSize = pn.widgets.IntSlider(name='Point Size', start=10, end=100, value=10)
stateSelector = pn.widgets.Select(name='State', value='CA', options=states)
goesPtColor = pn.widgets.Select(name='GOES Fire Point Color', value='g', options=markercolor_iter)
modPtColor = pn.widgets.Select(name='MODIS Fire Point Color', value='b', options=markercolor_iter)
viirsPtColor = pn.widgets.Select(name='VIIRS Fire Points Color', value='k', options=markercolor_iter)
timeAveragedSequentialRadioGroup.link(layersGroup, callbacks={'value': sequentialDisable})
timeAveragedSequentialRadioGroup.link(markerSize, callbacks={'value': sequentialDisable})
timeAveragedSequentialRadioGroup.link(goesPtColor, callbacks={'value': sequentialDisable})
timeAveragedSequentialRadioGroup.link(modPtColor, callbacks={'value': sequentialDisable})
timeAveragedSequentialRadioGroup.link(viirsPtColor, callbacks={'value': sequentialDisable})
toggleClip = pn.widgets.Toggle(name='Clip Raster to State', button_type='success')
toggleCoastlineV1 = pn.widgets.Toggle(name='Add coastlines', button_type='default')
toggleCSVExport = pn.widgets.Button(name='Export to time series to CSV', button_type='success')
rasterSelector = pn.widgets.Select(name='Raster Variable', value='IMERG.FINAL.v6 Fire Weather Index', options=list(dataDict.keys()))
addTimeSeries = pn.widgets.MultiChoice(name='Additional Time Series Plots', value=['IMERG.FINAL.v6 Fire Weather Index'], options=list(dataDict.keys()))
title = pn.pane.Markdown('# EIS FIRE - Mult-variable raster and time series visualization', width=600)
subtitle = pn.pane.Markdown('This interactive dashboard displays raster data in an interactive format. This raster data may be clipped to individual states via user-controls. In addition this dashboard displays various time-series of user-given data products. These time-series are averaged over individual state polygons. All TROPOMI data is unfiltered L2 gridded data')

In [12]:
@pn.depends(dateTime=dateTimeSelector.param.value, rasterLN=rasterSelector.param.value,
            cmap=cmapSelector.param.value, cmapReverse=toggleCmapReverseV1.param.value,
            state=stateSelector.param.value, coastline=toggleCoastlineV1.param.value,
           climMin=userMin.param.value, climMax=userMax.param.value, 
            markerSize=markerSize.param.value, clipRaster=toggleClip.param.value,
            addTS=addTimeSeries.param.value, goesPtC=goesPtColor.param.value, 
            modPtC=modPtColor.param.value, viirsPtC=viirsPtColor.param.value,
           exportToCSV=toggleCSVExport.param.value, rasterType=timeAveragedSequentialRadioGroup.param.value,
           step=timeStepInput, layers=layersGroup.param.value)
def visuaPanel(dateTime, rasterLN, cmap, state, markerSize,addTS,clipRaster, cmapReverse, 
               coastline,goesPtC,modPtC,viirsPtC,climMin,climMax,exportToCSV, rasterType, step, layers):
    raster_clim = None if (climMin==0 and climMax==0) else (climMin, climMax)
    timeAve = True if rasterType=='Time Averaged' else False
    dateTime = pandas.to_datetime(dateTime)
    raster=dataDict[rasterLN]['shortName']
    tropo=dataDict[rasterLN]['tropomiSet']
    rasterToUse = tropoDataset[raster] if tropo else mergedDataset[raster]
    rasterToUse = clip_to_shape(rasterToUse, land_shp)
    cmap = cmap+'_r' if cmapReverse else cmap
    shp_layer = get_shp_layer(engine, state)
    raster_clipped = clip_to_shape(rasterToUse, shp_layer)
    raster_to_use = raster_clipped if clipRaster else rasterToUse
    layer_plt = plot_layer(shp_layer, 800)
    if not timeAve:
        if 'NIFC Perimeter Polygons' in layers:
            nifcData = getNIFCByDate(dateTime, dateTime)
            nifcPlot = nifcData.hvplot(geo=True,
                                       coastline=coastline,
                                       color=nifcData['Shape__Area'],
                                       hover_cols=['OBJECTID', 'poly_Incidentname'],
                                       projection=projection,
                                       colorbar=False)
        raster = raster_to_use.sel(time=dateTime).load().hvplot(
            cmap=cmap,
            coastline=coastline,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
        if 'Active Fire Points' in layers:
            shp_data = get_shp_data(dateTime, engine, place=state)
            shp_goes, shp_mod, shp_v = split_shp_data(shp_data)
            points_goes = plot_points(shp_goes, 800, projection, markerSize, goesPtC)
            points_mod = plot_points(shp_mod, 800, projection, markerSize, modPtC)
            points_viirs = plot_points(shp_v, 800, projection, markerSize, viirsPtC)
            if 'NIFC Perimeter Polygons' in layers:
                plot = (raster * points_goes * points_mod * points_viirs * layer_plt * nifcPlot).opts(
                    title='{} {} Date: {}'.format(rasterLN, dataDict[rasterLN]['units'], dateTime))
            else:
                plot = (raster * points_goes * points_mod * points_viirs * layer_plt).opts(
                    title='{} {} Date: {}'.format(rasterLN, dataDict[rasterLN]['units'], dateTime))
        else:
            plot = (raster * layer_plt * nifcPlot) if 'NIFC Perimeter Polygons' in layers else (raster * layer_plt)
            plot = plot.opts(title='{} {} Date: {}'.format(rasterLN, dataDict[rasterLN]['units'], dateTime))
    else:
        raster = raster_to_use.load().hvplot(
            groupby='time',
            cmap=cmap,
            coastline=coastline,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
        plot = (raster * layer_plt).opts(
            title='{} {}'.format(rasterLN, dataDict[rasterLN]['units']))
    # Plotting time series
    col = pn.Column(pn.Card(plot))
    tsCard = pn.Card(title='Time Series')
    for ts in addTS:
        color=line_color_iter[random.randint(0, len(line_color_iter)-1)]
        varShortName = dataDict[ts]['shortName']
        tropo = dataDict[ts]['tropomiSet']
        rasterTS = mergedDataset[varShortName] if not tropo else tropoDataset[varShortName]
        rasterTS = rasterTS.resample(time=step).mean(dim='time') if timeAve else rasterTS
        if dataDict[ts]['collapse']:
            ds = collapseTo1D(clip_to_shape(rasterTS, shp_layer))
            if exportToCSV:
                ds.to_pandas().to_csv('{}_{}.csv'.format(varShortName, state))
            addTimeSeriesPlot = ds.hvplot.line('time', color=color)
        else:
            meanDs = collapseMean(clip_to_shape(rasterTS, shp_layer))
            if exportToCSV:
                meanDs.to_pandas().to_csv('{}_{}.csv'.format(varShortName, state))
            addTimeSeriesPlot = meanDs.hvplot.line('time', color=color, title='{} {}'.format(
                                                                    ts, dataDict[ts]['units']))
        tsCard.append(addTimeSeriesPlot)
    col.append(tsCard)
    return col

In [13]:
accordion = pn.Accordion(
            ('Layers', layersGroup),
            ('Time Averaged Control', timeStepInput),
            ('ColorMap', pn.Column(cmapSelector,toggleCmapReverseV1)),
            ('Polygon Selection', pn.Column(stateSelector)),
            ('Raster Customization', pn.Column(toggleCoastlineV1, toggleClip, pn.Row(userMin, userMax))),
            ('Active Fire Point Plotting', pn.Column(markerSize, goesPtColor, modPtColor, viirsPtColor)), 
    header_background='#0059b3', header_color='white', active_header_background='#339966')
titleRow = pn.Row(pn.Column(title, subtitle))
widgetBox = pn.WidgetBox(pn.Column(timeAveragedSequentialRadioGroup, 
                                rasterSelector, 
                                accordion, 
                                addTimeSeries, 
                                dateTimeSelector, toggleCSVExport), height=800)#, title='Control Panel')
dashboard = pn.Column(titleRow, pn.Row(widgetBox, visuaPanel), background='WhiteSmoke')
print('Rendering')
dashboard

Rendering


Column(background='WhiteSmoke')
    [0] Row
        [0] Column
            [0] Markdown(str, width=600)
            [1] Markdown(str)
    [1] Row
        [0] WidgetBox(height=800)
            [0] Column
                [0] RadioButtonGroup(button_type='success', name='Visualization Type', options=['Date-Time Sequential', ...], value='Date-Time Sequential')
                [1] Select(name='Raster Variable', options=['IMERG.FINAL.v6 Fire Weat...], value='IMERG.FINAL.v6 F...)
                [2] Accordion(active_header_background='#339966', header_background='#0059b3', header_color='white')
                    [0] CheckBoxGroup(name='Layers', options=['Active Fire Points', ...])
                    [1] TextInput(disabled=True, name='Time Step', value='7D')
                    [2] Column
                        [0] Select(name='Colormap Selector', options=['kbc', 'fire', ...], value='fire')
                        [1] Toggle(name='Reverse colormap')
                    [3] Column
                        [0] Select(name='State', options=['AL', 'AK', 'AZ', ...], value='CA')
                    [4] Column
                        [0] Toggle(name='Add coastlines')
                        [1] Toggle(button_type='success', name='Clip Raster to State')
                        [2] Row
                            [0] IntInput(name='Min', width=60)
                            [1] IntInput(name='Max', width=60)
                    [5] Column
                        [0] IntSlider(end=100, name='Point Size', start=10, value=10)
                        [1] Select(name='GOES Fire Point Color', options=['r', 'b', 'g', 'k', 'z'], value='g')
                        [2] Select(name='MODIS Fire Point Color', options=['r', 'b', 'g', 'k', 'z'], value='b')
                        [3] Select(name='VIIRS Fire Points Color', options=['r', 'b', 'g', 'k', 'z'], value='k')
                [3] MultiChoice(name='Additional Time S..., options=['IMERG.FINAL.v6 Fire Weat...], value=['IMERG.FINAL.v6 F...])
                [4] DateSlider(end=datetime.datetime(2020, ..., name='DateTime Selector', start=datetime.datetime(2020, ..., value=datetime.datetime(2020, ...)
                [5] Button(button_type='success', name='Export to time s...)
        [1] ParamFunction(function)

# Visualization 2 - Multi-Time Series Panel

In [15]:
stateSelectorMTS = pn.widgets.Select(name='State', value='CA', options=states)
exportCSVMTS = pn.widgets.Button(name='Export to CSV', button_type='success')
titleMTS = pn.pane.Markdown('# Multi-variable time series panel', width=800)
subtitleMTS = pn.pane.Markdown("These time series are averaged over the given state's polygon.", width=800)
@pn.depends(state=stateSelectorMTS.param.value, exportToCSV=exportCSVMTS.param.value)
def plotTimeSeriesPanel(state='CA', exportToCSV=False):
    shp_layer = get_shp_layer(engine, state)
    sumCBiomass = collapseTo1D(clip_to_shape(mergedDataset['co.biomass'], shp_layer))
    sumC = collapseTo1D(clip_to_shape(mergedDataset['c'], shp_layer))
    fwi = clip_to_shape(mergedDataset['IMERG.FINAL.v6_FWI'], shp_layer).mean(['lat', 'lon'])
    t2m = clip_to_shape(mergedDataset['T2M'], shp_layer).mean(['lat', 'lon'])
    activeFires = queryActiveFires(queryEngine=engine, stateSelect=True, state=state, dateEnd=date_end)
    activeFires.rename(columns={'date':'time'}, inplace=True)
    activeFires.set_index('time', inplace=True)
    xraf = xr.Dataset.from_dataframe(activeFires)
    if exportToCSV:
        activeFires.to_csv('{}_{}.csv'.format('MOD_ACTIVE_FIRES', state))
        sumCBiomass.to_pandas().to_csv('{}_{}.csv'.format('COBIOMASS', state))
        sumC.to_pandas().to_csv('{}_{}.csv'.format('c', state))
        fwi.to_pandas().to_csv('{}_{}.csv'.format('FWI', state))
        t2m.to_pandas().to_csv('{}_{}.csv'.format('T2M', state))
    vizActiveFires = xraf.hvplot.line(x='time', y='count', title='MOD14 Active Fires')
    vizCBiomass = sumCBiomass.hvplot.line(title='CO2 Biomass Emissions kg s-1 m-2', color='r').opts(bgcolor='lightgray')
    vizC = sumC.hvplot.line(title='c', color='b')
    vizFWI = fwi.hvplot.line(title='IMERG.FINAL.v6 Fire Weather Index', color='g').opts(bgcolor='lightgray')
    vizT2M = t2m.hvplot.line(title='2-meter_air_temperature K', color='y').opts(bgcolor='lightgray')
    col = pn.Row(pn.Column(vizCBiomass, vizC, vizT2M), pn.Column(vizActiveFires, vizFWI))
    return col 

In [16]:
pn.Column(pn.Row(pn.Column(titleMTS, subtitleMTS)), pn.Row(pn.Column(stateSelectorMTS, exportCSVMTS)), pn.Card(plotTimeSeriesPanel))

Column
    [0] Row
        [0] Column
            [0] Markdown(str, width=800)
            [1] Markdown(str, width=800)
    [1] Row
        [0] Column
            [0] Select(name='State', options=['AL', 'AK', 'AZ', ...], value='CA')
            [1] Button(button_type='success', name='Export to CSV')
    [2] Card
        [0] ParamFunction(function)

## Visualization 3 - Animation by time step

Time series animation. It should be noted that if rasters are particularly large, then the animation will run slow and may skip time steps.

Use the play/pause widget to play through the animation. <b>Be aware that calculations can make the animation lag at times</b>.

In [17]:
timeStepInputAnim = pn.widgets.TextInput(name='Time Step', value='7D', disabled=True)
userMinAnim = pn.widgets.IntInput(name='Min', width=60)
userMaxAnim = pn.widgets.IntInput(name='Max', width=60)
cmapSelectorAnim = pn.widgets.Select(name='Colormap Selector', value='fire', options=cmaps_str)
toggleCmapReverseAnim = pn.widgets.Toggle(name='Reverse colormap', button_type='default')
stateSelectorAnim = pn.widgets.Select(name='State', value='CA', options=states)
toggleClipAnim = pn.widgets.Toggle(name='Clip Raster to State', button_type='success')
toggleCoastlineAnim = pn.widgets.Toggle(name='Add coastlines', button_type='default')
rasterSelectorAnim = pn.widgets.Select(name='Raster Variable', value='IMERG.FINAL.v6 Fire Weather Index', options=list(dataDict.keys()))
titleAnim = pn.pane.Markdown('# EIS FIRE - Mult-variable raster animation', width=600)
subtitleAnim = pn.pane.Markdown('This interactive dashboard displays raster data in an interactive format. This raster data may be clipped to individual states via user-controls. In addition this dashboard displays various time-series of user-given data products. These time-series are averaged over individual state polygons. All TROPOMI data is unfiltered L2 gridded data')

In [18]:
@pn.depends(rasterLN=rasterSelectorAnim.param.value,
            cmap=cmapSelector.param.value, cmapReverse=toggleCmapReverseAnim.param.value,
            state=stateSelectorAnim.param.value, coastline=toggleCoastlineAnim.param.value,
           climMin=userMinAnim.param.value, climMax=userMaxAnim.param.value, 
            clipRaster=toggleClipAnim.param.value)
def animVisual(climMin, climMax, cmap, cmapReverse, state, clipRaster, coastline, rasterLN):
    raster_clim = None if (climMin==0 and climMax==0) else (climMin, climMax)
    raster=dataDict[rasterLN]['shortName']
    tropo=dataDict[rasterLN]['tropomiSet']
    rasterToUse = tropoDataset[raster] if tropo else mergedDataset[raster]
    rasterToUse = clip_to_shape(rasterToUse, land_shp)
    #rasterToUse = landClippedRasters[raster]
    cmap = cmap+'_r' if cmapReverse else cmap
    shp_layer = get_shp_layer(engine, state)
    raster_clipped = clip_to_shape(rasterToUse, shp_layer)
    raster_to_use = raster_clipped if clipRaster else rasterToUse
    raster = raster_to_use.hvplot(
        groupby='time',
        cmap=cmap,
        coastline=True,
        frame_width=800,
        clim=raster_clim,
        projection=projection,
        widget_type='scrubber',
        widget_location='bottom')
    plot = (raster)
    col = pn.Column(pn.Card(plot))
    return col

In [19]:
accordionAnim = pn.Accordion(
            ('ColorMap', pn.Column(cmapSelectorAnim,toggleCmapReverseV1)),
            ('Polygon Selection', pn.Column(stateSelectorAnim)),
            ('Raster Customization', pn.Column(toggleCoastlineAnim, toggleClipAnim, pn.Row(userMinAnim, userMaxAnim))),
    header_background='#0059b3', header_color='white', active_header_background='#339966')
titleRowAnim = pn.Row(pn.Column(titleAnim, subtitleAnim))
widgetBoxAnim = pn.WidgetBox(pn.Column(
                                rasterSelectorAnim, 
                                accordionAnim), height=500)#, title='Control Panel')
dashboardAnim = pn.Column(titleRowAnim, pn.Row(widgetBoxAnim, animVisual), background='WhiteSmoke')
dashboardAnim

Column(background='WhiteSmoke')
    [0] Row
        [0] Column
            [0] Markdown(str, width=600)
            [1] Markdown(str)
    [1] Row
        [0] WidgetBox(height=500)
            [0] Column
                [0] Select(name='Raster Variable', options=['IMERG.FINAL.v6 Fire Weat...], value='IMERG.FINAL.v6 F...)
                [1] Accordion(active_header_background='#339966', header_background='#0059b3', header_color='white')
                    [0] Column
                        [0] Select(name='Colormap Selector', options=['kbc', 'fire', ...], value='fire')
                        [1] Toggle(name='Reverse colormap')
                    [1] Column
                        [0] Select(name='State', options=['AL', 'AK', 'AZ', ...], value='CA')
                    [2] Column
                        [0] Toggle(name='Add coastlines')
                        [1] Toggle(button_type='success', name='Clip Raster to State')
                        [2] Row
                            [0] IntInput(name='Min', width=60)
                            [1] IntInput(name='Max', width=60)
        [1] ParamFunction(function)

## Visualization 4 - Anomaly Maps

Use the scrubber widget at the bottom to move through time by anomaly time-step defined in code cell five.

Controls to the right of the visual allow you to zoom, move, and save. Hover over the visual to see the variable on-hover.

In [20]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v6 = False

# (lower_bound, upper_bound)
custom_range_v6 = (0, 5)

In [23]:
anomaly = main_raster.groupby('time.month') - \
    main_raster.groupby('time.month').mean('time')

In [24]:
def visual_six(cmap, dt, state):
    raster_clim = get_clim(anomaly) if not custom_range_bool_v6 else custom_range_v6
    shp_layer = get_shp_layer(engine, state)
    raster_clipped = clip_to_shape(anomaly, shp_layer)
    anomaly_clim = custom_range_v6 if custom_range_bool_v6 else get_clim(raster_clipped)
    raster = raster_clipped.sel(time=dt).hvplot(
        cmap=cmap,
        coastline=True,
        frame_width=800,
        clim=anomaly_clim,
        projection=projection)
    
    layer = shp_layer.hvplot(
        frame_width=800,
        color='None')
    
    plot = (raster * layer).opts(title='{} Anomaly, Dt: {}'.format(raster_variable_to_show, dt))
    
    return plot

In [25]:
kdims_list_six = ['cmap', 'dt', 'state']
dynamic_viz_six = hv.DynamicMap(visual_six, kdims=kdims_list_six)
dynamic_viz_six.redim.values(cmap=cmaps, dt=daterange_iter, state=states)

:DynamicMap   [cmap,dt,state]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]
      .Polygons.I  :Polygons   [x,y]

## Visualization 5 - Lat/Lon averaged per day.

Use the controls to the right of the visual to zoom, move around, and save.

In [26]:
main_raster.hvplot.scatter('time', groupby=[], datashade=True) *\
main_raster.mean(['lat', 'lon']).hvplot.line('time', yaxis='right', color='indianred')

:DynamicMap   []
   :Overlay
      .RGB.I   :RGB   [time,IMERG.FINAL.v6_FWI]   (R,G,B,A)
      .Curve.I :Curve   [time]   (IMERG.FINAL.v6_FWI)

## Visualization 6 - User-defined polygon

In [27]:
timeAveragedSequentialRadioGroupUser = pn.widgets.RadioButtonGroup(
 name='Visualization Type', options=['Date-Time Sequential', 'Time Averaged'], value='Date-Time Sequential', button_type='success')
layersGroupUser = pn.widgets.CheckBoxGroup(name='Layers', options=['NIFC Perimeter Polygons', 'Raster', 'Time Series'], value=['Raster', 'Time Series'])
timeStepInputUser = pn.widgets.TextInput(name='Time Step', value='7D', disabled=True)
timeAveragedSequentialRadioGroupUser.link(timeStepInputUser, callbacks={'value': timeAveragedCallBack})
userMinUser = pn.widgets.IntInput(name='Min', width=60)
userMaxUser = pn.widgets.IntInput(name='Max', width=60)
cmapSelectorUser = pn.widgets.Select(name='Colormap Selector', value='fire', options=cmaps_str)
toggleCmapReverseUser = pn.widgets.Toggle(name='Reverse colormap', button_type='default')
dateTimeSelectorUser = pn.widgets.DateSlider(name='DateTime Selector', start=d_s, end=d_e, value=datetime(2020, 8, 10))
timeAveragedSequentialRadioGroupUser.link(dateTimeSelectorUser, callbacks={'value': sequentialDisable})
toggleClipUser = pn.widgets.Toggle(name='Clip raster to polygon', button_type='success')
toggleCoastlineUser = pn.widgets.Toggle(name='Add coastlines', button_type='default')
toggleCSVExportUser = pn.widgets.Button(name='Export to time series to CSV', button_type='success')
rasterSelectorUser = pn.widgets.Select(name='Raster Variable', value='IMERG.FINAL.v6 Fire Weather Index', options=list(dataDict.keys()))
addTimeSeriesUser = pn.widgets.MultiChoice(name='Additional Time Series Plots', value=['IMERG.FINAL.v6 Fire Weather Index'], options=list(dataDict.keys()))
titleUser = pn.pane.Markdown('# User-defined polygon visualization', width=600)
subtitleUser = pn.pane.Markdown('This interactive dashboard displays raster data in an interactive format. This raster data may be clipped to individual states via user-controls. In addition this dashboard displays various time-series of user-given data products. These time-series are averaged over individual state polygons.')
visual_iter = ['Raster Variable', 'Time-Averaged (month)', 'Anomaly']
watercolor = basemap_to_tiles(basemaps.Esri.WorldImagery)
m = Map(layers=(watercolor, ), center=(39.59, -98.26), zoom=4)

draw_control = DrawControl()

draw_control.polygon = {
    "shapeOptions": {
        "fillColor": "#6be5c3",
        "color": "#6be5c3",
        "fillOpacity": 0.2
    },
    "drawError": {
        "color": "#dd253b",
        "message": "Oups!"
    },
    "allowIntersection": False
}

draw_control.rectangle = {
    "shapeOptions": {
        "fillColor": "#fca45d",
        "color": "#fca45d",
        "fillOpacity": 0.2
    }
}

feature_collection = {
    'type': 'FeatureCollection',
    'features': []
}

def handle_draw(self, action, geo_json):
    """Do something with the GeoJSON when it's drawn on the map"""
    feature_collection['features'].append(geo_json)
    df_gpd = gpd.GeoDataFrame.from_features(feature_collection)

draw_control.on_draw(handle_draw)
m.add_control(draw_control)

m

Map(center=[39.59, -98.26], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [28]:
@pn.depends(dateTime=dateTimeSelectorUser.param.value, rasterLN=rasterSelectorUser.param.value,
            cmap=cmapSelectorUser.param.value, cmapReverse=toggleCmapReverseUser.param.value, 
            coastline=toggleCoastlineUser.param.value,
           climMin=userMinUser.param.value, climMax=userMaxUser.param.value, 
            clipRaster=toggleClipUser.param.value,
            addTS=addTimeSeriesUser.param.value,
           exportToCSV=toggleCSVExportUser.param.value, rasterType=timeAveragedSequentialRadioGroupUser.param.value,
           step=timeStepInputUser, layers=layersGroupUser.param.value)
def visuaPanelUserDef(dateTime, rasterLN, cmap, addTS,clipRaster, cmapReverse, 
               coastline, climMin,climMax,exportToCSV, rasterType, step, layers, featureCollection=feature_collection):
    dfToUse = gpd.GeoDataFrame.from_features(featureCollection)
    if climMin==0 and climMax==0:
        raster_clim=None
    else:
        raster_clim=(climMin, climMax)
    timeAve = True if rasterType=='Time Averaged' else False
    dateTime = pandas.to_datetime(dateTime)
    if 'Raster' in layers:
        raster=dataDict[rasterLN]['shortName']
        tropo=dataDict[rasterLN]['tropomiSet']
        rasterToUse = tropoDataset[raster] if tropo else mergedDataset[raster]
        rasterToUse = clip_to_shape(rasterToUse, land_shp)
        raster_clipped = clip_to_shape(rasterToUse, dfToUse)
        cmap = cmap+'_r' if cmapReverse else cmap
        raster_to_use = raster_clipped if clipRaster else rasterToUse
        layer_plt = plot_layer(dfToUse, 800)
        if not timeAve:
            raster = raster_to_use.sel(time=dateTime).hvplot(
                cmap=cmap,
                coastline=coastline,
                frame_width=800,
                clim=raster_clim,
                projection=projection)
            plot = (raster * layer_plt).opts(title='{} {} Date: {}'.format(rasterLN, dataDict[rasterLN]['units'], dateTime))
        else:
            raster = raster_to_use.hvplot(
                groupby='time',
                cmap=cmap,
                coastline=coastline,
                frame_width=800,
                clim=raster_clim,
                projection=projection)
            plot = (raster * layer_plt).opts(
                title='{} {}'.format(rasterLN, dataDict[rasterLN]['units']))
        # Plotting time series
        col = pn.Column(pn.Card(plot))
    else:
        col = pn.Column()
    if 'Time Series' in layers:
        tsCard = pn.Card(title='Time Series')
        for ts in addTS:
            color=line_color_iter[random.randint(0, len(line_color_iter)-1)]
            varShortName = dataDict[ts]['shortName']
            tropo = dataDict[ts]['tropomiSet']
            rasterTS = mergedDataset[varShortName] if not tropo else tropoDataset[varShortName]
            rasterTS = rasterTS.resample(time=step).mean(dim='time') if timeAve else rasterTS
            if dataDict[ts]['collapse']:
                ds = collapseTo1D(clip_to_shape(rasterTS, dfToUse))
                if exportToCSV:
                    ds.to_pandas().to_csv('{}_{}.csv'.format(varShortName, state))
                addTimeSeriesPlot = ds.hvplot.line('time', color=color)
            else:
                ds = clip_to_shape(rasterTS, dfToUse)
                meanDs = ds.mean(['lat', 'lon'])
                if exportToCSV:
                    meanDs.to_pandas().to_csv('{}_{}.csv'.format(varShortName, state))
                addTimeSeriesPlot = meanDs.hvplot.line('time', color=color, title='{} {}'.format(
                ts, dataDict[ts]['units']))
            tsCard.append(addTimeSeriesPlot)
        col.append(tsCard)
    return col

accordionUser = pn.Accordion(
            ('Layers', layersGroupUser),
            ('Time Averaged Control', timeStepInputUser),
            ('ColorMap', pn.Column(cmapSelectorUser,toggleCmapReverseUser)),
            ('Raster Customization', pn.Column(toggleCoastlineUser, toggleClipUser, pn.Row(userMinUser, userMaxUser))),
    header_background='#0059b3', header_color='white', active_header_background='#339966')
titleRowUser = pn.Row(pn.Column(titleUser, subtitleUser))
widgetBoxUser = pn.WidgetBox(pn.Column(timeAveragedSequentialRadioGroupUser, 
                                rasterSelectorUser, 
                                accordionUser, 
                                addTimeSeriesUser, 
                                dateTimeSelectorUser, toggleCSVExportUser), height=1000)#, title='Control Panel')
dashboardUser = pn.Column(titleRowUser, pn.Row(widgetBoxUser, visuaPanelUserDef), background='WhiteSmoke')
dashboardUser

Column(background='WhiteSmoke')
    [0] Row
        [0] Column
            [0] Markdown(str, width=600)
            [1] Markdown(str)
    [1] Row
        [0] WidgetBox(height=1000)
            [0] Column
                [0] RadioButtonGroup(button_type='success', name='Visualization Type', options=['Date-Time Sequential', ...], value='Date-Time Sequential')
                [1] Select(name='Raster Variable', options=['IMERG.FINAL.v6 Fire Weat...], value='IMERG.FINAL.v6 F...)
                [2] Accordion(active_header_background='#339966', header_background='#0059b3', header_color='white')
                    [0] CheckBoxGroup(name='Layers', options=['NIFC Perimeter Polygons'...], value=['Raster', 'Time Series'])
                    [1] TextInput(disabled=True, name='Time Step', value='7D')
                    [2] Column
                        [0] Select(name='Colormap Selector', options=['kbc', 'fire', ...], value='fire')
                        [1] Toggle(name='Reverse colormap')
                    [3] Column
                        [0] Toggle(name='Add coastlines')
                        [1] Toggle(button_type='success', name='Clip raster to polygon')
                        [2] Row
                            [0] IntInput(name='Min', width=60)
                            [1] IntInput(name='Max', width=60)
                [3] MultiChoice(name='Additional Time S..., options=['IMERG.FINAL.v6 Fire Weat...], value=['IMERG.FINAL.v6 F...])
                [4] DateSlider(end=datetime.datetime(2020, ..., name='DateTime Selector', start=datetime.datetime(2020, ..., value=datetime.datetime(2020, ...)
                [5] Button(button_type='success', name='Export to time s...)
        [1] ParamFunction(function)